In [1]:
import pandas as pd
import wandb
import pprint
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score

In [2]:
wandb.init(name='load_tweet_dataset_1',
                 project='epfl_ml_project2', 
                 tags=['load_dataset'],
                 job_type='for_testing')
artifact = wandb.use_artifact('hsunyu/epfl_ml_project2/twitter_dataset_1:v0')
artifact_dir = artifact.download()
wandb.finish()

wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb: Currently logged in as: cr7_reunited (cr7_reunited-cr7). Use `wandb login --relogin` to force relogin


wandb:   3 of 3 files downloaded.  


In [3]:
wandb.login()

True

In [4]:
# load it into a pandas dataframe
train_df = pd.read_json(artifact_dir + '/train.json', lines=True)
val_df = pd.read_json(artifact_dir + '/val.json', lines=True)
test_df = pd.read_json(artifact_dir + '/test.json', lines=True)

In [5]:
sweep_config = {
    'method': 'grid'
}

metric = {
    'name': 'val_accuracy',
    'goal': 'maximize'
}

parameters_dict = {
    'dataset': {
        'values': ['bow', 'tfidf']
    },
    'n_estimators': {
        'values': [1, 10, 50, 100, 250, 500]
    },
    'criterion': {
        'values': ['gini', 'entropy', 'log_loss']
    },
    'max_depth': {
        'values': [3, 6, 15, 20, 30, 50, 100, None]
    },
    'min_samples_leaf': {
        'values': [1, 2, 4, 10]
    }
}

sweep_config['metric'] = metric
sweep_config['parameters'] = parameters_dict

In [6]:
pprint.pprint(sweep_config)

{'method': 'grid',
 'metric': {'goal': 'maximize', 'name': 'val_accuracy'},
 'parameters': {'criterion': {'values': ['gini', 'entropy', 'log_loss']},
                'dataset': {'values': ['bow', 'tfidf']},
                'max_depth': {'values': [3, 6, 15, 20, 30, 50, 100, None]},
                'min_samples_leaf': {'values': [1, 2, 4, 10]},
                'n_estimators': {'values': [1, 10, 50, 100, 250, 500]}}}


In [7]:
sweep_id = wandb.sweep(sweep_config, project='epfl_ml_project2')

Create sweep with ID: al89gxt6
Sweep URL: https://wandb.ai/cr7_reunited-cr7/epfl_ml_project2/sweeps/al89gxt6


In [8]:
bow = CountVectorizer()
tfidf = TfidfVectorizer()

In [9]:
train_sentences = train_df['sentence1'].tolist()
val_sentences = val_df['sentence1'].tolist()
test_sentences = test_df['sentence1'].tolist()

In [10]:
y_train = train_df['label'].values
y_val = val_df['label'].values
y_test = test_df['label'].values

In [11]:
X_train_bow = bow.fit_transform(train_sentences)
X_val_bow = bow.transform(val_sentences)
X_test_bow = bow.transform(test_sentences)

In [12]:
X_train_tfidf = tfidf.fit_transform(train_sentences)
X_val_tfidf = tfidf.transform(val_sentences)
X_test_tfidf = tfidf.transform(test_sentences)

In [13]:
def return_dataset(dataset):
    if dataset == 'bow':
        return X_train_bow, X_val_bow, X_test_bow, y_train, y_val, y_test
    return X_train_tfidf, X_val_tfidf, X_test_tfidf, y_train, y_val, y_test

In [14]:
def train(config=None):
    with wandb.init(config=config):
        config = wandb.config
        X_train, X_val,_ , y_train, y_val, _ = return_dataset(config.dataset)
        clf = RandomForestClassifier(n_estimators=config.n_estimators, criterion=config.criterion, max_depth=config.max_depth, min_samples_leaf=config.min_samples_leaf, n_jobs=-1, random_state=599131614)
        clf.fit(X_train, y_train)
        wandb.log({'train_accuracy': accuracy_score(y_train, clf.predict(X_train)), 'val_accuracy': accuracy_score(y_val, clf.predict(X_val))})

In [15]:
wandb.agent(sweep_id, train)

wandb: Agent Starting Run: negtjvef with config:
wandb: 	criterion: gini
wandb: 	dataset: bow
wandb: 	max_depth: 3
wandb: 	min_samples_leaf: 1
wandb: 	n_estimators: 1


wandb: Agent Starting Run: hc5v8eoc with config:
wandb: 	criterion: gini
wandb: 	dataset: bow
wandb: 	max_depth: 3
wandb: 	min_samples_leaf: 1
wandb: 	n_estimators: 10


wandb: Agent Starting Run: eofa2h9j with config:
wandb: 	criterion: gini
wandb: 	dataset: bow
wandb: 	max_depth: 3
wandb: 	min_samples_leaf: 1
wandb: 	n_estimators: 50


wandb: Agent Starting Run: 2uthmth0 with config:
wandb: 	criterion: gini
wandb: 	dataset: bow
wandb: 	max_depth: 3
wandb: 	min_samples_leaf: 1
wandb: 	n_estimators: 100


wandb: Agent Starting Run: pnd0bjxw with config:
wandb: 	criterion: gini
wandb: 	dataset: bow
wandb: 	max_depth: 3
wandb: 	min_samples_leaf: 1
wandb: 	n_estimators: 250


...

wandb: Agent Starting Run: rq6vjyj6 with config:
wandb: 	criterion: log_loss
wandb: 	dataset: tfidf
wandb: 	max_depth: None
wandb: 	min_samples_leaf: 10
wandb: 	n_estimators: 50


wandb: Agent Starting Run: z8xe9byn with config:
wandb: 	criterion: log_loss
wandb: 	dataset: tfidf
wandb: 	max_depth: None
wandb: 	min_samples_leaf: 10
wandb: 	n_estimators: 100


wandb: Agent Starting Run: jvjm8x6m with config:
wandb: 	criterion: log_loss
wandb: 	dataset: tfidf
wandb: 	max_depth: None
wandb: 	min_samples_leaf: 10
wandb: 	n_estimators: 250


wandb: Agent Starting Run: d67vux2j with config:
wandb: 	criterion: log_loss
wandb: 	dataset: tfidf
wandb: 	max_depth: None
wandb: 	min_samples_leaf: 10
wandb: 	n_estimators: 500


wandb: Sweep Agent: Waiting for job.
wandb: Sweep Agent: Exiting.


In [16]:
api = wandb.Api()
sweep = api.sweep(f'cr7_reunited-cr7/epfl_ml_project2/sweeps/{sweep_id}')

# Get best run parameters
best_run = sweep.best_run(order='val_accuracy')
best_params = best_run.config
print(best_params)

wandb: Sorting runs by -summary_metrics.val_accuracy


{'min_samples_leaf': 1, 'dataset': 'bow', 'criterion': 'log_loss', 'max_depth': None, 'n_estimators': 500}


In [17]:
X_train, _, X_test, y_train, _, y_test = return_dataset(best_params['dataset'])
clf = RandomForestClassifier(n_estimators=best_params['n_estimators'], criterion=best_params['criterion'], max_depth=best_params['max_depth'], min_samples_leaf=best_params['min_samples_leaf'], n_jobs=-1, random_state=599131614)
clf.fit(X_train, y_train)
print(accuracy_score(y_train, clf.predict(X_train)))
print(accuracy_score(y_test, clf.predict(X_test)))

0.9996333333333334
0.809875
